Create the Table, load it and browse sample data

In [ ]:
CREATE TABLE electricity_consumption
(usage_datetime timestamp, 
consumptioninkw float, 
customer_id varchar(24)
);

COPY electricity_consumption
FROM 's3://redshift-blogs/redshift-ml-deep-dive-workshop/electricityusagedata/electricityusagedata.csv'
IAM_ROLE default
REGION 'us-east-1' delimiter ',' IGNOREHEADER 1;

Select customer_id,usage_datetime,consumptioninkw
from "dev"."public"."electricity_consumption"
order by 1,2

Now let's create the forecast model

In [ ]:
CREATE MODEL forecast_electricity_consumption
FROM electricity_consumption 
TARGET consumptioninkw 
IAM_ROLE 'arn:aws:your-IAM-Role'
AUTO ON MODEL_TYPE FORECAST
SETTINGS (S3_BUCKET 'your-S3-bucket-name',
 HORIZON 24,
 FREQUENCY 'H',
 S3_GARBAGE_COLLECT OFF);

Check Model S

In [ ]:
show MODEL forecast_electricity_consumption;

Generating Forecast Data

In [ ]:
CREATE TABLE forecast_electricty_predictions AS SELECT FORECAST(forecast_electricity_consumption);

Check Forecast data for the next 24 hours

In [ ]:
Select id, "time", p10,p50,p90, (p10+p50+p90)/3 as med
from "dev"."public"."forecast_electricty_predictions"
order by 1,2